# **AutoDriveRL**
- Author: Kim Dohwan [@ehghks021203](https://github.com/ehghks021203)
- Date: 2024.03.14. ~
- Description: DQN 알고리즘을 활용한 자율주행 모델 개발

여기서는 CARLA Simulation 클라이언트를 사용하여 자율주행 모델을 학습하는 과정을 설명합니다. DQN(Deep Q-Network) 알고리즘을 사용하여 자율주행 에이전트를 학습시키며, 이미지 처리를 위한 ShuffleNet과 웨이포인트 처리를 위한 GRU가 결합된 멀티모달 신경망 **MixxNet**을 모델로 활용합니다.


## **Abstract**

자율주행 에이전트의 학습과 개발은 복잡한 과제입니다. 본 프로젝트는 DQN 알고리즘을 사용하여 자율주행 에이전트가 장애물 회피, 차선 유지, 신호 준수와 같은 목표를 달성하는 모델을 개발하는 것을 목적으로 합니다. 이를 통해 안전하고 효율적인 주행을 실현합니다.


## **Objective and Significance**

본 연구의 주요 목표는 자율주행 모델의 성능을 향상시키는 것입니다. 이를 달성하기 위한 구체적인 목표는 다음과 같습니다.

1. **장애물 회피:** 에이전트가 도로 상의 장애물을 정확히 인식하고 피할 수 있도록 합니다.
2. **차선 유지:** 에이전트가 주어진 차선을 안정적으로 유지하며 주행할 수 있도록 합니다.
3. **신호 준수:** 교통 신호를 인식하고 이를 준수하는 능력을 향상시킵니다.
4. **효율적 주행:** 안전한 범위 내에서 빠르고 효율적으로 주행하도록 에이전트를 학습시킵니다.


## **Neural Network Architecture**
### **MixxNet**

MixxNet은 이미지 데이터를 처리하는 **ShuffleNet**과 경로 데이터를 처리하는 **GRU**로 구성된 멀티모달 신경망입니다. 이 네트워크의 목적은 자율주행 환경에서 카메라 이미지와 웨이포인트 데이터를 함께 처리하여 더 나은 주행 예측을 수행하는 것입니다.

- **ShuffleNet:** 경량화된 CNN 아키텍처로 이미지 데이터를 입력받아 유의미한 특징을 추출합니다.
- **GRU:** 주행 경로 데이터를 시퀀스 형태로 처리하여 시간에 따른 변화를 고려합니다.

두 가지 신경망의 출력을 결합하여 최종 행동(action)을 결정합니다.


## **DQN Algorithm**

DQN은 강화 학습 기반의 알고리즘으로, 에이전트가 환경과 상호작용하면서 최적의 행동 정책을 학습합니다. 주요 개념은 다음과 같습니다.

1. **상태(state):** 에이전트가 현재 인식하고 있는 환경의 정보입니다 (이미지 및 웨이포인트).
2. **행동(action):** 에이전트가 취할 수 있는 행동으로, 가속, 브레이크, 조향 등이 있습니다.
3. **보상(reward):** 에이전트가 특정 행동을 취했을 때 환경으로부터 받는 피드백입니다.
4. **정책(policy):** 에이전트가 각 상태에서 어떤 행동을 선택할지 결정하는 전략입니다.

DQN은 리플레이 메모리(Replay Memory)와 타깃 네트워크(Target Network)를 활용하여 안정적으로 학습합니다. 또한, 에이전트는 매 프레임마다 환경에서 수집한 데이터를 이용해 Q-값을 갱신하고, 최적의 정책을 학습합니다.


## **Reward Functions**

자율주행 에이전트가 다양한 주행 상황에서 최적의 행동을 선택할 수 있도록, 다음과 같은 보상 함수가 설정되었습니다:

- **장애물 회피 보상:** 장애물을 성공적으로 회피할 때 높은 보상을 부여.
- **차선 유지 보상:** 차선을 안정적으로 유지할 때 보상.
- **신호 준수 보상:** 교통 신호를 적절히 준수할 때 보상.
- **효율적 주행 보상:** 주어진 목표 시간 안에 빠르고 안전하게 목적지에 도달할 때 보상.

보상 함수는 에이전트가 올바른 주행 행동을 강화하고, 불필요한 충돌이나 잘못된 주행을 피하도록 유도합니다.


In [1]:
!python -V

Python 3.7.16


In [2]:
# Add file path
import os
import sys
sys.path.append(os.path.dirname(os.path.abspath('')))
import subprocess

# Define the command and parameters
command = [
    'CarlaUE4.exe',  # Executable
    '-windowed',     # Parameters
    '-ResX=640',
    '-ResY=480',
    '-quality-level=Low',
    '-benchmark',
    '-fps=30'
]

# Run the command in the background
process = subprocess.Popen(command, cwd='E:\\CARLA_SIM', shell=True)

# Now you can run other cells without being blocked
print("CarlaUE4.exe is running in the background.")

CarlaUE4.exe is running in the background.


## **1. CARLA Client and World Setup**

### **1.1 CARLA Client Initialization**

CARLA 클라이언트에 연결해 가상환경을 설정합니다. 클라이언트는 가상환경의 시간, 날씨, 교통 등을 제어할 수 있습니다.

- Client Host: `localhost`
- Client Port: `2000`

In [3]:
import carla

client = carla.Client("localhost", 2000)
client.set_timeout(50)

### **1.2 World and Sensor Initialization**

시뮬레이션 월드를 로드하고, 맵 데이터를 가져오며, 블루프린트 라이브러리를 불러옵니다.

In [4]:
# Set world
world = client.load_world("Town04_Opt")
world.unload_map_layer(carla.MapLayer.Decals)

# Get map data
map = world.get_map()

# Get blueprint library
blueprint_library = world.get_blueprint_library()

## **2. Agent and Waypoint Class declarations**

에이전트와 웨이포인트 클래스는 자율주행 시스템의 핵심 구성 요소입니다.

### **2.1 Agent Class**

에이전트(Agent)는 자율주행 차량으로, 환경으로부터 센서 데이터를 받아 처리하고 행동을 결정합니다.

차량의 속도, 위치, 방향을 제어하는 메서드를 포함합니다.


In [5]:
import time
import math
import cv2
import numpy as np

class Agent():
    def __init__(self, world, blueprint_library, waypoint) -> None:
        # Initialize
        self.world = world
        self.blueprint_library = blueprint_library
        self.front_image = None
        self.collision_hist = []

        # Initialize actor list
        self.actor_list = []
        
        # Set vehicle spawn point
        self.waypoint = waypoint
        self.transform = self.waypoint.start_point
        self.vehicle_model = blueprint_library.filter("vehicle.mini.cooper_s_2021")[0]

        # Spawning the vehicle
        self.vehicle = world.spawn_actor(self.vehicle_model, self.transform)
        self.actor_list.append(self.vehicle)
        
        # Attach Camera with Vehicle
        self.rgb_cam = world.spawn_actor(
            blueprint_library.find('sensor.camera.rgb'),
            carla.Transform(carla.Location(x=1.5, z=2.4), carla.Rotation(pitch=-15)),
            attach_to=self.vehicle
        )
        self.rgb_cam.listen(self._process_img)
        self.actor_list.append(self.rgb_cam)

        # Observer Camera
        self.observe_cam = world.spawn_actor(
            blueprint_library.find('sensor.camera.rgb'),
            carla.Transform(carla.Location(x=-1.5, z=17.8), carla.Rotation(pitch=-90)),
            attach_to=self.vehicle
        )
        self.actor_list.append(self.observe_cam)
        
        # Attach Collision Sensor with Vehicle
        self.collision_sensor = world.spawn_actor(
            blueprint_library.find('sensor.other.collision'),
            carla.Transform(),
            attach_to=self.vehicle
        )
        self.collision_sensor.listen(self._collision_data)
        self.actor_list.append(self.collision_sensor)

        self.target_speed = 30

    def get_route(self, max_point=10, draw=False, to_list=True):
        if not self.waypoint:
            raise RuntimeError("Waypoint does not exist")
        agent_location = self.get_location()
        waypoint_data = []
        min_dist = 99999999
        min_idx = 0
        for i in range(len(self.waypoint.waypoints)):
            x = self.waypoint.waypoints[i][0].transform.location.x - agent_location.x
            y = self.waypoint.waypoints[i][0].transform.location.y - agent_location.y
            waypoint_data.append([x, y])
            dist = math.sqrt(x**2 + y**2)
            if min_dist > dist:
                min_dist = dist 
                min_idx = i
        if draw:
            first_point = True
            for w in self.waypoint.waypoints[min_idx:min_idx+max_point]:
                if first_point:
                    self.world.debug.draw_string(
                        w[0].transform.location, 
                        'O', 
                        draw_shadow=False,
                        color=carla.Color(r=0, g=255, b=0), 
                        life_time=0.5,
                        persistent_lines=True
                    )
                    first_point = False
                else:
                    self.world.debug.draw_string(
                        w[0].transform.location, 
                        'O', 
                        draw_shadow=False,
                        color=carla.Color(r=255, g=0, b=0), 
                        life_time=0.2,
                        persistent_lines=True
                    )

        if to_list:
            return np.array(waypoint_data[min_idx:min_idx+max_point])
        else:
            return self.waypoint.waypoints[min_idx:min_idx+max_point]

    def get_travel_distance(self):
        if not self.waypoint:
            raise RuntimeError("Waypoint does not exist")
        agent_location = self.get_location()
        min_dist = 99999999
        min_idx = 0
        for i in range(len(self.waypoint.waypoints)):
            x = self.waypoint.waypoints[i][0].transform.location.x - agent_location.x
            y = self.waypoint.waypoints[i][0].transform.location.y - agent_location.y
            dist = math.sqrt(x**2 + y**2)
            if min_dist > dist:
                min_dist = dist 
                min_idx = i
        return min_idx / len(self.waypoint.waypoints)

    def get_location(self):
        return self.vehicle.get_location()

    def get_transform(self):
        return self.vehicle.get_transform()

    def get_speed(self):
        """
        Compute speed of a vehicle in Km/h.
            :param vehicle: the vehicle for which speed is calculated
            :return: speed as a float in Km/h
        """
        vel = self.vehicle.get_velocity()
    
        return 3.6 * math.sqrt(vel.x**2 + vel.y**2 + vel.z**2)

    def apply_control(self, throttle, brake, steer):
        self.vehicle.apply_control(carla.VehicleControl(throttle=throttle, brake=brake, steer=steer))

    def set_waypoint(self, waypoint):
        self.waypoint = waypoint

    def _process_img(self, image):
        array = np.frombuffer(image.raw_data, dtype=np.dtype("uint8"))
        array = np.reshape(array, (image.height, image.width, 4))
        array = array[:, :, :3]
        array = array[:, :, ::-1]
    
        dim = (128, 128)  # set same dim for now
        resized_img = cv2.resize(array, dim, interpolation=cv2.INTER_AREA)
        img_gray = cv2.cvtColor(resized_img, cv2.COLOR_BGR2GRAY)
        scaledImg = img_gray/255.
    
        # normalize
        mean, std = 0.5, 0.5
        self.front_image = (scaledImg - mean) / std


    def _collision_data(self, event):
        # What we collided with and what was the impulse
        collision_actor_id = event.other_actor.type_id
        collision_impulse = math.sqrt(event.normal_impulse.x**2 + event.normal_impulse.y**2 + event.normal_impulse.z**2)

        # Add collision
        self.collision_hist.append(event)


    def destroy(self):
        for actor in self.actor_list:
            actor.destroy()

### **2.2 Waypoint Class**

웨이포인트(Waypoint)는 자율주행 경로 상의 좌표의 집합으로, 에이전트의 목적지를 설정하고 경로를 잘 따르는지 확인하기 위해 사용됩니다.

웨이포인트 간의 거리, 방향을 계산하고 업데이트하느 메서드들이 포함됩니다.

In [6]:
from src.agents.navigation.global_route_planner import GlobalRoutePlanner

class Waypoint():
    def __init__(self, stt_point=10, end_point=20):
        self.sampling_resolution = 2
        self.grp = GlobalRoutePlanner(map, self.sampling_resolution)
        spawn_points = map.get_spawn_points()
        
        self.start_point = spawn_points[stt_point]
        self.end_point = spawn_points[end_point]
        self.start_point_location = carla.Location(self.start_point.location)
        self.end_point_location = carla.Location(self.end_point.location)
        self.waypoints = self.grp.trace_route(self.start_point_location, self.end_point_location)

    def render(self):
        i = 0
        for w in self.waypoints:
            if i % 10 == 0:
                world.debug.draw_string(
                    w[0].transform.location, 
                    'O', 
                    draw_shadow=False,
                    color=carla.Color(r=255, g=0, b=0), 
                    life_time=2.0,
                    persistent_lines=True
                )
            else:
                world.debug.draw_string(
                    w[0].transform.location, 
                    'O', 
                    draw_shadow=False,
                    color = carla.Color(r=0, g=0, b=255), 
                    life_time=2.0,
                    persistent_lines=True
                )
            time.sleep(0.05)
            i += 1

    def show_spawn_points(self):
        spawn_points = map.get_spawn_points()
        for i in range(len(spawn_points)):
            world.debug.draw_string(
                spawn_points[i].location, 
                f'{i}', 
                draw_shadow=False,
                color=carla.Color(r=255, g=0, b=0), 
                life_time=2.0,
                persistent_lines=True
            )

In [7]:
waypoint = Waypoint(stt_point=12, end_point=285)
waypoint.render()

## **3. MixxNet: Multi-Modal Neural Network for Autonomous Driving**

`MixxNet`은 이미지와 경로 데이터를 동시에 처리하는 멀티모달 신경망입니다.

### **3.1 CNN-based Image Processing**

차량의 전방 이미지를 처리하여 도로, 장애물, 차선 등 환경의 특징을 추출합니다.

ShuffleNet과 같은 경량 CNN을 사용하여 실시간 처리 속도를 높입니다.

### **3.2 GRU-based Waypoint Processing**

GRU 네트워크를 사용하여 웨이포인트 데이터를 처리하고, 이들 다음 행동에 반영합니다.

### **3.3 Combining the Two Networks**

CNN과 GRU의 출력을 결합하여 최종 행동을 결정하는 데 사용합니다.

### Model Structure
`MixxNet`은 이미지 데이터를 처리하는 `CNN`과 경로 데이터를 처리하는 `GRU`로 구성됩니다. 이 두 출력을 결합하여 전결합층(Fully-Connected Layer)을 통해 최종 예측을 수행합니다.

### Input Parameters
- `num_actions`: 신경망의 출력 차원
- `in_channels`: 입력 이미지의 채널 수
- `input_size`: 각 입력 벡터의 크기
- `hidden_size`: GRU의 은닉 상태 벡터 크기
- `num_layers`: GRU의 레이어 수
- `seq_length`: 입력 시퀀스의 길이


In [8]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torchvision.models import shufflenet_v2_x0_5

class MixxNet(nn.Module):
    def __init__(self, num_actions, in_channels, input_size, hidden_size, num_layers, seq_length) -> None:
        super(MixxNet, self).__init__()

        # ShuffleNet V2 for image data
        self.shufflenet = shufflenet_v2_x0_5(pretrained=True)
        
        # Adjust input channels to match ShuffleNetV2's expectation (3 channels)
        self.input_conv = nn.Conv2d(in_channels, 3, kernel_size=1, stride=1, padding=0, bias=False)

        # CNN output size adaptation
        self.shufflenet_fc = nn.Linear(1000, 256)  # ShuffleNet x0.5 output dimension

        # GRU for waypoint data
        self.gru = nn.GRU(input_size=input_size, hidden_size=hidden_size, num_layers=num_layers, batch_first=True)

        # Fully connected layers for GRU output
        self.gru_fc = nn.Linear(hidden_size, 32)  # GRU output size

        # Layer normalization for ShuffleNet output
        self.shufflenet_norm = nn.LayerNorm(256)

        # Fully connected layers for combined outputs
        self.fc_layer1 = nn.Sequential(
            nn.Linear(256 + 32, 128),  # Reduce dimensions for efficiency
            nn.ReLU(),
            nn.LayerNorm(128)
        )
        self.fc_layer2 = nn.Sequential(
            nn.Linear(128, 64),  # Reduce dimensionality to balance complexity
            nn.ReLU(),
            nn.LayerNorm(64)
        )
        self.fc_layer3 = nn.Linear(64, num_actions)  # Final layer for actions

    def forward(self, image_data, waypoint_data):
        # Adjust image data channels
        image_data = self.input_conv(image_data)

        # ShuffleNet forward pass
        shufflenet_out = self.shufflenet(image_data)
        shufflenet_out = shufflenet_out.view(shufflenet_out.size(0), -1)  # Flatten
        shufflenet_out = F.relu(self.shufflenet_fc(shufflenet_out))
        shufflenet_out = self.shufflenet_norm(shufflenet_out)

        # GRU forward pass
        h_0 = torch.zeros(self.gru.num_layers, waypoint_data.size(0), self.gru.hidden_size, device=waypoint_data.device)
        gru_out, _ = self.gru(waypoint_data, h_0)
        gru_out = gru_out[:, -1, :]  # Take the output of the last time step
        gru_out = F.relu(self.gru_fc(gru_out))

        # Combine ShuffleNet and GRU outputs
        combined = torch.cat((shufflenet_out, gru_out), dim=1)

        # Fully connected layers
        x = self.fc_layer1(combined)
        x = self.fc_layer2(x)
        output = self.fc_layer3(x)

        return output


## **DQNAgent with MixxNet**

자율주행에 발생하는 복잡한 제어 문제를 해결하기 위해 DQN 에이전트를 사용합니다.
앞서 구성한 `MixxNet`을 사용하여 이미지 데이터와 경로 데이터를 처리합니다.

<br/>

### Model Structure
`DQNAgent`는 Deep Q-Network 알고리즘을 기반으로 하는 에이전트입니다. 이 에이전트는 `MixxNet`을 사용하여 상태를 입력으로 받아 최적의 행동을 출력합니다.

### MixxNet
`MixxNet`은 이미지 데이터를 처리하는 CNN과 경로 데이터를 처리하는 GRU로 구성됩니다. 두 출력을 결합하여 최종 예측을 수행합니다.

### DQNAgent Functions
#### 1. 모델 초기화 (`__init__`)
- 모델의 하이퍼파라미터를 설정합니다.
- MixxNet을 Q Network로 초기화하고, 이를 복사하여 타겟 네트워크를 만듭니다.
- 옵티마이저를 설정합니다.

#### 2. 액션 선택 함수 (`select_action`)
- 현재 상태에서 최적의 행동을 선택합니다.
- `eval`이 `True`인 경우, 평가 모드에서 행동을 선택합니다.
- Epsilon-greedy 정책을 사용하여 행동을 선택합니다.

#### 3. 학습 함수 (`train`)
- 리플레이 메모리에서 미니배치를 샘플링하여 네트워크를 학습시킵니다.
- 현재 Q 값과 타겟 Q 값을 계산하여 손실을 구합니다.
- 옵티마이저를 사용하여 손실을 최소화합니다.
- 일정 주기마다 타겟 네트워크를 업데이트합니다.

#### 4. 타겟 네트워크 업데이트 함수 (`copy_target_update`)
- 일정 주기마다 타겟 네트워크를 Q 네트워크의 가중치로 업데이트합니다.

#### 5. 모델 저장 함수 (`save`)
- Q 네트워크와 옵티마이저 상태를 저장합니다.

#### 6. 모델 로드 함수 (`load`)
- 저장된 Q 네트워크와 옵티마이저 상태를 불러옵니다.


In [9]:
import copy

class DQNAgent(object):
    def __init__(
        self,
        num_actions,
        in_channels,
        waypoint_dim,
        device,
        discount=0.9,
        optimizer="Adam",
        optimizer_parameters={'lr':0.01},
        target_update_frequency=1e4,
        initial_eps=1,
        end_eps=0.05,
        eps_decay_period=25e4,
        eval_eps=0.001
    ) -> None:
        # Set Device
        self.device = device
        self.num_actions = num_actions

        # Initialize MixxNet as Q network
        self.Q = MixxNet(
            num_actions=num_actions,  # Output for throttle, brake, and steer
            in_channels=in_channels, 
            input_size=2, 
            hidden_size=128,
            num_layers=2,
            seq_length=10
        ).to(self.device)
        self.Q_target = copy.deepcopy(self.Q)  # Copy target network
        self.Q_optimizer = getattr(torch.optim, optimizer)(self.Q.parameters(), **optimizer_parameters)

        self.discount = discount
        self.target_update_frequency = target_update_frequency
 
        # Epsilon decay
        self.initial_eps = initial_eps
        self.end_eps = end_eps
        self.slope = (self.end_eps - self.initial_eps) / eps_decay_period

        self.state_shape = (in_channels, 128, 128)  # Example image shape
        self.eval_eps = eval_eps
        self.iterations = 0

    def select_action(self, image_state, waypoint_state, eval=False):
        print("1.1 enter select action")
        eps = self.eval_eps if eval else max(self.slope * self.iterations + self.initial_eps, self.end_eps)
        self.current_eps = eps
        print("1.2 set eps")

        # Select action according to policy with probability (1-eps)
        # Otherwise, select random action
        if np.random.uniform(0, 1) > eps:
            self.Q.eval()
            print("1.3 Q eval")
            with torch.no_grad():
                image_state = torch.FloatTensor(image_state).reshape(self.state_shape).unsqueeze(0).to(self.device)
                print("1.4 image state")
                waypoint_state = torch.FloatTensor(waypoint_state).unsqueeze(0).to(self.device)
                print("1.5 waypoint state")
                # Assuming image_state has shape [128, 128] and needs to be reshaped to [1, 1, 128, 128]
                # image_state = torch.FloatTensor(image_state).unsqueeze(0).to(self.device)
                # Assuming waypoint_state has shape [waypoint_dim]
                # waypoint_state = torch.FloatTensor(waypoint_state).to(self.device)
                return int(self.Q(image_state, waypoint_state).argmax(1))
        else:
            return np.random.randint(self.num_actions)

    def train(self, replay_memory):
        self.Q.train()
        image_state, waypoint_state, action, next_image_state, next_waypoint_state, reward, done = replay_memory.sample()

        action = action.clone().detach().long()

        with torch.no_grad():
            target_Q = reward + (1 - done) * self.discount * self.Q_target(next_image_state, next_waypoint_state).max(1, keepdim=True)[0]

        # Get current Q estimate
        # torch gather just selects action values from Q(state) using the action tensor as an index
        current_Q = self.Q(image_state, waypoint_state).gather(1, action)

        # Compute Q loss
        Q_loss = F.smooth_l1_loss(current_Q, target_Q)

        # Optimize the Q
        self.Q_optimizer.zero_grad()
        Q_loss.backward()
        self.Q_optimizer.step()

        # Update target network by full copy every X iterations.
        self.iterations += 1
        self.copy_target_update()

    def copy_target_update(self):
        if self.iterations % self.target_update_frequency == 0:
            print('target network updated')
            print('current epsilon', self.current_eps)
            self.Q_target.load_state_dict(self.Q.state_dict())

    def save(self, filename):
        torch.save(self.Q.state_dict(), filename + "_Q")
        torch.save(self.Q_optimizer.state_dict(), filename + "_optimizer")

    def load(self, filename):
        self.Q.load_state_dict(torch.load(filename + "_Q"))
        self.Q_target = copy.deepcopy(self.Q)
        self.Q_optimizer.load_state_dict(torch.load(filename + "_optimizer"))


## **Replay memory**

In [10]:
class ReplayMemory(object):
    def __init__(
        self,
        image_dim,
        waypoint_dim,
        batch_size,
        buffer_size,
        device
    ) -> None:
        self.batch_size = batch_size
        self.max_size = int(buffer_size)
        self.device = device

        self.ptr = 0
        self.crt_size = 0

        # Initialize buffers
        self.image_state = np.zeros((self.max_size,) + image_dim)
        self.waypoint_state = np.zeros((self.max_size,) + waypoint_dim)
        self.action = np.zeros((self.max_size, 3))
        self.next_image_state = np.zeros((self.max_size,) + image_dim)
        self.next_waypoint_state = np.zeros((self.max_size,) + waypoint_dim)
        self.reward = np.zeros((self.max_size, 1))
        self.done = np.zeros((self.max_size, 1))

    def add(self, image_state, waypoint_state, action, next_image_state, next_waypoint_state, reward, done):
        self.image_state[self.ptr] = image_state
        self.waypoint_state[self.ptr] = waypoint_state
        self.action[self.ptr] = action
        self.next_image_state[self.ptr] = next_image_state
        self.next_waypoint_state[self.ptr] = next_waypoint_state
        self.reward[self.ptr] = reward
        self.done[self.ptr] = done

        self.ptr = (self.ptr + 1) % self.max_size
        self.crt_size = min(self.crt_size + 1, self.max_size)

    def sample(self):
        ind = np.random.randint(0, self.crt_size, size=self.batch_size)
        return (
            torch.FloatTensor(self.image_state[ind]).unsqueeze(1).to(self.device),
            torch.FloatTensor(self.waypoint_state[ind]).to(self.device),
            torch.FloatTensor(self.action[ind]).to(self.device),
            torch.FloatTensor(self.next_image_state[ind]).unsqueeze(1).to(self.device),
            torch.FloatTensor(self.next_waypoint_state[ind]).to(self.device),
            torch.FloatTensor(self.reward[ind]).to(self.device),
            torch.FloatTensor(self.done[ind]).to(self.device)
        )


## **Reward Function**

In [11]:
def get_reward_comp(vehicle, waypoint, is_collision):
    vehicle_location = vehicle.get_location()
    x_wp = waypoint[1][0].transform.location.x
    y_wp = waypoint[1][0].transform.location.y

    x_vh = vehicle_location.x
    y_vh = vehicle_location.y

    wp_array = np.array([x_wp, y_wp])
    vh_array = np.array([x_vh, y_vh])

    dist = np.linalg.norm(wp_array - vh_array)

    vh_yaw = correct_yaw(vehicle.get_transform().rotation.yaw)
    wp_yaw = correct_yaw(waypoint[1][0].transform.rotation.yaw)
    cos_yaw_diff = np.cos((vh_yaw - wp_yaw)*np.pi/180.)

    collision = 1 if is_collision else 0

    travel_distance = vehicle.get_travel_distance()

    speed = -1 if vehicle.get_speed() <= 20 else 1

    reward = cos_yaw_diff - dist - (3 * collision) + speed + (5 * travel_distance)
    
    return reward

def correct_yaw(x):
    return(((x%360) + 360) % 360)


In [12]:
# dqn action values with stop action
action_values = [
    (1.00, 0.00, 0.00),  # Forward
    (0.00, 0.00, -1.00), # Left
    (0.00, 0.00, 1.00),  # Right
    (1.00, 0.00, -1.00), # Forward left
    (1.00, 0.00, 1.00),  # Forward right 
    (0.00, 1.00, 0.00),  # Brake
    (0.00, 1.00, -1.00), # Brake left
    (0.00, 1.00, 1.00),  # Brake right
    (0.00, 0.00, 0.00),  # Stop action
]

action_values = [
    (0.00, 0.00, 0.00),  # Stop action
    (1.00, 0.00, -0.75), 
    (1.00, 0.00, -0.50), 
    (1.00, 0.00, -0.25), 
    (1.00, 0.00, -0.15), 
    (1.00, 0.00, -0.10), 
    (1.00, 0.00, -0.05), 
    (1.00, 0.00, 0.00),
    (1.00, 0.00, 0.05), 
    (1.00, 0.00, 0.10),
    (1.00, 0.00, 0.50), 
    (1.00, 0.00, 0.75),
]

action_map = {i: x for i, x in enumerate(action_values)}
num_actions = len(action_values)

In [13]:
params = {
    "eval": False,
    "fps": 60,
    "image_dim": (128, 128),
    "waypoint_dim": (10, 2),
    "batch_size": 16,
    "buffer_size": 1e4,
    "start_ep": 0,
    "end_ep": 5000,
    "train_freq": 2,
    "save_freq": 100,
    "start_ep": 0,
    "start_buffer": 10,
}

start_train = params["start_ep"] + params["start_buffer"]

In [14]:
import matplotlib.pyplot as plt
import seaborn as sns
from collections import deque
import time
from threading import Thread

agent_list = []

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
replay_memory = ReplayMemory(
    image_dim=params["image_dim"],
    waypoint_dim=params["waypoint_dim"],
    batch_size=params["batch_size"],
    buffer_size=params["buffer_size"],
    device=device
)
model = DQNAgent(
    num_actions=num_actions,
    in_channels=1,
    waypoint_dim=params["waypoint_dim"],
    device=device
)

episode = params["start_ep"]
global_timestep = 0
ep_reward_list = []

# 
def train_model(replay_memory, model):
    while True:
        if not params["eval"] and episode > start_train and (global_timestep % params["train_freq"] == 0):
            model.train(replay_memory)
# Start train thread
training_thread = Thread(target=train_model, args=(replay_memory, model))
training_thread.start()

# Loop over episodes
try:
    while True:
        episode += 1
        # Environment reset
        for agent in agent_list:
            agent.destroy()
        agent_list = []
        print("## destroy agent")

        agent = Agent(world=world, blueprint_library=blueprint_library, waypoint=waypoint)
        agent_list.append(agent)

        print("## init agent")

        # For agent speed measurements - keeps last 60 frametimes
        fps_counter = deque(maxlen=60)

        step_count = 0
        episode_reward = 0

        # Get initial state
        current_image_state = agent.front_image
        current_waypoint_state = agent.get_route()
        print("## get init state")

        # Loop over steps
        while True:
            step_start = time.time()
            step_count += 1
            global_timestep += 1
            print("0. seta")

            # Predict an action based on current observation space
            action = model.select_action(current_image_state, current_waypoint_state, eval=params["eval"])
            throttle, brake, steer = action_map[action]
            print("1. get action & run action")

            # Step environment
            agent.apply_control(throttle, brake, steer)
            print("2. apply action")
            # Calculate speed in km/h from car's velocity
            kmh = agent.get_speed()
            # Get agent route and render
            agent_route = agent.get_route(to_list=False, draw=step_count % 10 == 0)
            print("3. get agent data")

            done = False
            is_collision = False

            if len(agent.collision_hist) != 0:
                done = True
                is_collision = True

            if step_count >= 1000:
                done = True
            print("4. check done condition")

            # Reward
            reward = get_reward_comp(agent, agent_route, is_collision)
            episode_reward += reward
            print("5. calculate reward")

            if done:
                print("Episode {:4d} processed {:5d} | reward: {}".format(episode, step_count, episode_reward))
                break

            next_image_state = agent.front_image
            next_waypoint_state = agent.get_route()
            print("6. get next state")

            replay_memory.add(current_image_state, current_waypoint_state, action, next_image_state, next_waypoint_state, reward, done)
            print("7. add replay memory")

            current_image_state = next_image_state
            current_waypoint_state = next_waypoint_state

            frame_time = time.time() - step_start
            fps_counter.append(frame_time)
            # This takes no time, so we add a delay matching 60 FPS (prediction above takes longer)
            if params["eval"] or episode < start_train or (global_timestep % params["train_freq"] != 0):
                time.sleep(1/params["fps"])
            print("8. end current step")
            
        if episode % params["save_freq"] == 0 and episode > params["start_ep"]:
            model.save(f"../weights/model_ep_{episode}")
            print("== Saved model ==")
        if episode >= params["end_ep"]:
            print("## episode end")
            break
finally:
    training_thread.join()
    print("=== END ===")
    plt.subplots(figsize=(10, 7))
    sns.lineplot(ep_reward_list, label="ep-reward")



c:\Users\ehghk\anaconda3\envs\autodrive\lib\site-packages\torchvision\models\_utils.py:209: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  f"The parameter '{pretrained_param}' is deprecated since 0.13 and may be removed in the future, "
c:\Users\ehghk\anaconda3\envs\autodrive\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ShuffleNet_V2_X0_5_Weights.IMAGENET1K_V1`. You can also use `weights=ShuffleNet_V2_X0_5_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


## destroy agent
## init agent
## get init state
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done conditio

c:\Users\ehghk\anaconda3\envs\autodrive\lib\site-packages\ipykernel_launcher.py:80: UserWarning: Using a target size (torch.Size([16, 1])) that is different to the input size (torch.Size([16, 3])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.


7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. calculate reward
6. get next state
7. add replay memory
8. end current step
0. seta
1. get action & run action
2. apply action
3. get agent data
4. check done condition
5. cal